In [1]:
import pandas as pd
import datetime, os
import numpy as np
import numpy.random as npr
from pylab import plt, mpl

from scipy.stats import norm
from scipy import optimize
import scipy.integrate as integrate
import scipy.special as special 

import tensorflow as tf
from tensorflow.keras.callbacks import EarlyStopping, TensorBoard
from tensorboard.plugins.hparams import api as hp
from tensorflow import keras
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.preprocessing import StandardScaler

import matplotlib.pyplot as plt
import seaborn as sns

# Load the TensorBoard notebook extension
%load_ext tensorboard

Lets save the dataframe as a CSV so we dont need to run it again, but can just load it when needed.

In [2]:
#To read the import the csv-file, use:
raw_Options = pd.read_csv (r"/Users/Marcklein/Desktop/Master Thesis/Option pricing using Neural Networks/Python/Heston/Heston_data.csv")

#Creates some unnamed column in the beginning, delete it:
del raw_Options['Unnamed: 0']


In [3]:
Options = raw_Options.copy()

Since the standard deviation is calculated by taking the sum of the squared deviations from the mean, a zero standard deviation can only be possible when all the values of a variable are the same (all equal to the mean). In this case, those variables have no discriminative power so they can be removed from the analysis. They cannot improve any classification, clustering or regression task. Many implementations will do it for you or throw an error about a matrix calculation.

In [4]:
Options.pop("S");

### **Data preparation**

We split our dataset into a training set and a test set (validation set is taken from the training set during model.fit).

In [5]:
# 90% for training and validating
train_dataset = Options.sample(frac=0.9, random_state=42)
test_dataset = Options.drop(train_dataset.index)

Check the overall statistics

In [6]:
train_stats = train_dataset.describe()
train_stats.pop("imp vol")
train_stats = train_stats.T
train_stats

count      mean       std       min       25%       50%       75%  \
tau    90000.0  0.602657  0.286360  0.109589  0.353425  0.602740  0.849315   
r      90000.0  0.049994  0.028822  0.000100  0.025000  0.050000  0.074900   
sigma  90000.0  0.275861  0.132868  0.050000  0.160000  0.280000  0.390000   
rho    90000.0 -0.450744  0.287163 -0.900000 -0.700000 -0.500000 -0.200000   
nu     90000.0  0.275315  0.132609  0.050000  0.160000  0.280000  0.390000   
theta  90000.0  0.275549  0.132575  0.050000  0.160000  0.280000  0.390000   
kappa  90000.0  0.999440  0.523035  0.100000  0.550000  1.000000  1.450000   
K      90000.0  1.025238  0.129826  0.800000  0.912847  1.025488  1.137419   

           max  
tau    1.09863  
r      0.10000  
sigma  0.50000  
rho    0.00000  
nu     0.50000  
theta  0.50000  
kappa  1.90000  
K      1.25000

Separate the target values from the input values. These values are the values that we will train the model to predict. We will also normalize the data due to reasons described in the thesis

In [7]:
train_labels = train_dataset.pop("imp vol").values
test_labels = test_dataset.pop("imp vol").values

In [8]:

#normalize the data
def norm(x):
    return (x - train_stats['mean']) / train_stats['std']
normed_train_data = norm(train_dataset).values
normed_test_data = norm(test_dataset).values


'''
#standardise the data
scaler = StandardScaler()
normed_train_data = scaler.fit_transform(train_dataset)
normed_test_data = scaler.fit_transform(test_dataset)

'''
#check the shapes
print(normed_train_data.shape)
print(normed_test_data.shape)

(90000, 8)
(10000, 8)


### **The hyperparameter testing-model**

We start by initializing all the hyperparameters that we want to asses. We then set the metrics of the model to "mean squared error". Since Tensorboard works with log files that are created during the training process we create logs for the training process that records the losses, metrics and other measures during training.

In [16]:
#The hyperparameters & their values to be tested are stored in a special type called HParam
HP_NUM_UNITS = hp.HParam('num_units', hp.Discrete([250, 500, 750, 1000]))
HP_DROPOUT = hp.HParam('dropout', hp.RealInterval(0.1, 0.3))
HP_OPTIMIZER = hp.HParam('optimizer', hp.Discrete(['adam', 'sgd']))

#Setting the Metric to MSE (Mean Squared Error)
METRIC_MSE = 'mean_squared_error'

# Clear any logs from previous runs
!rm -rf ./logs/ 

#Creating & configuring log files
with tf.summary.create_file_writer('logs/hparam_tuning').as_default():
    hp.hparams_config(
        hparams=[HP_NUM_UNITS, HP_DROPOUT, HP_OPTIMIZER],
        metrics=[hp.Metric(METRIC_MSE, display_name='mean_squared_error')],
        )

Now we create a function to train and validate the model which will take the hyperparameters as arguments. Each combination of hyperparameters will run for # epochs and the hyperparameters are provided in an hparams dictionary and used throughout the training function

In [17]:
#A function that trains and validates the model and returns the MSE
def train_val_model(hparams):
    #Keras sequential model with Hyperparameters passed from the argument
    model = keras.models.Sequential([
            #Layer to be used as an entry point into a Network
            keras.layers.InputLayer(input_shape=[len(train_dataset.keys())]),
            #Dense layer
            keras.layers.Dense(hparams[HP_NUM_UNITS], activation='relu'),
            #Dropout layer
            keras.layers.Dropout(hparams[HP_DROPOUT], seed=42),
            #activation function is linear since we are doing regression
            keras.layers.Dense(1, activation='linear')
            ])
    
    #Compiling the model
    model.compile(optimizer=hparams[HP_OPTIMIZER], 
                  loss='mean_squared_error', 
                  metrics=['mean_squared_error'])
    
    early_stopping = EarlyStopping(monitor='val_loss', patience=1)
    
     #Training the network
    model.fit(normed_train_data, train_labels, 
         batch_size=100, 
         epochs=5,
         verbose=2,
         validation_split=0.2,
         callbacks=[early_stopping])
    
    _, mse = model.evaluate(normed_test_data, test_labels)
    return mse

The following function will initiate the training process with the hyperparameters to be assessed and will create a summary based on the RMSE value returned by the train_test_model function and writes the summary with the hyperparameters and final accuracy(MSE) in logs.

In [18]:
def run(run_dir, hparams):
    with tf.summary.create_file_writer(run_dir).as_default():
        hp.hparams(hparams)  # record the values used in this trial
        mse = train_val_model(hparams)
        tf.summary.scalar(METRIC_MSE, mse, step=10)

We will now train the model for each combination of the hyperparameters

In [22]:
#A unique number for each training session
session_num = 0

#Nested for loop training with all possible  combinathon of hyperparameters
for num_units in HP_NUM_UNITS.domain.values:
    for dropout_rate in (HP_DROPOUT.domain.min_value, HP_DROPOUT.domain.max_value):
        for optimizer in HP_OPTIMIZER.domain.values:
            hparams = {
                HP_NUM_UNITS: num_units,
                HP_DROPOUT: dropout_rate,
                HP_OPTIMIZER: optimizer,
            }
            run_name = "run-%d" % session_num
            print('--- Starting trial: %s' % run_name)
            print({h.name: hparams[h] for h in hparams})
            run('logs/hparam_tuning/' + run_name, hparams)
            session_num += 1


--- Starting trial: run-0
{'num_units': 250, 'dropout': 0.1, 'optimizer': 'adam'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 6s 89us/sample - loss: 0.0088 - mean_squared_error: 0.0088 - val_loss: 4.4426e-04 - val_mean_squared_error: 4.4426e-04
Epoch 2/5
72000/72000 [==============================] - 11s 156us/sample - loss: 0.0015 - mean_squared_error: 0.0015 - val_loss: 1.2912e-04 - val_mean_squared_error: 1.2912e-04
Epoch 3/5
72000/72000 [==============================] - 7s 94us/sample - loss: 6.1603e-04 - mean_squared_error: 6.1603e-04 - val_loss: 5.8961e-05 - val_mean_squared_error: 5.8961e-05
Epoch 4/5
72000/72000 [==============================] - 5s 70us/sample - loss: 3.5381e-04 - mean_squared_error: 3.5381e-04 - val_loss: 6.0012e-05 - val_mean_squared_error: 6.0012e-05
10000/1 [=========================================================================================================================================

--- Starting trial: run-1
{'num_units': 250, 'dropout': 0.1, 'optimizer': 'sgd'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 6s 87us/sample - loss: 0.0172 - mean_squared_error: 0.0172 - val_loss: 0.0031 - val_mean_squared_error: 0.0031
Epoch 2/5
72000/72000 [==============================] - 5s 74us/sample - loss: 0.0083 - mean_squared_error: 0.0083 - val_loss: 0.0017 - val_mean_squared_error: 0.0017
Epoch 3/5
72000/72000 [==============================] - 5s 72us/sample - loss: 0.0066 - mean_squared_error: 0.0066 - val_loss: 0.0011 - val_mean_squared_error: 0.0011
Epoch 4/5
72000/72000 [==============================] - 5s 71us/sample - loss: 0.0055 - mean_squared_error: 0.0055 - val_loss: 8.5471e-04 - val_mean_squared_error: 8.5471e-04
Epoch 5/5
72000/72000 [==============================] - 5s 72us/sample - loss: 0.0047 - mean_squared_error: 0.0047 - val_loss: 6.7375e-04 - val_mean_squared_error: 6.7375e-04
10000/1 [====

--- Starting trial: run-2
{'num_units': 250, 'dropout': 0.3, 'optimizer': 'adam'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 7s 93us/sample - loss: 0.0156 - mean_squared_error: 0.0156 - val_loss: 6.8789e-04 - val_mean_squared_error: 6.8789e-04
Epoch 2/5
72000/72000 [==============================] - 5s 76us/sample - loss: 0.0021 - mean_squared_error: 0.0021 - val_loss: 1.4051e-04 - val_mean_squared_error: 1.4051e-04
Epoch 3/5
72000/72000 [==============================] - 5s 75us/sample - loss: 8.7976e-04 - mean_squared_error: 8.7976e-04 - val_loss: 7.2341e-05 - val_mean_squared_error: 7.2341e-05
Epoch 4/5
72000/72000 [==============================] - 5s 75us/sample - loss: 5.0299e-04 - mean_squared_error: 5.0299e-04 - val_loss: 5.1163e-05 - val_mean_squared_error: 5.1163e-05
Epoch 5/5
72000/72000 [==============================] - 6s 81us/sample - loss: 3.2079e-04 - mean_squared_error: 3.2079e-04 - val_loss: 9.1619e-05 -

--- Starting trial: run-3
{'num_units': 250, 'dropout': 0.3, 'optimizer': 'sgd'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 7s 92us/sample - loss: 0.0300 - mean_squared_error: 0.0300 - val_loss: 0.0027 - val_mean_squared_error: 0.0027
Epoch 2/5
72000/72000 [==============================] - 5s 71us/sample - loss: 0.0139 - mean_squared_error: 0.0139 - val_loss: 0.0014 - val_mean_squared_error: 0.0014
Epoch 3/5
72000/72000 [==============================] - 5s 72us/sample - loss: 0.0092 - mean_squared_error: 0.0092 - val_loss: 8.3079e-04 - val_mean_squared_error: 8.3079e-04
Epoch 4/5
72000/72000 [==============================] - 5s 70us/sample - loss: 0.0064 - mean_squared_error: 0.0064 - val_loss: 5.6007e-04 - val_mean_squared_error: 5.6007e-04
Epoch 5/5
72000/72000 [==============================] - 5s 71us/sample - loss: 0.0047 - mean_squared_error: 0.0047 - val_loss: 4.2557e-04 - val_mean_squared_error: 4.2557e-04
10000

--- Starting trial: run-4
{'num_units': 500, 'dropout': 0.1, 'optimizer': 'adam'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 8s 114us/sample - loss: 0.0053 - mean_squared_error: 0.0053 - val_loss: 2.2466e-04 - val_mean_squared_error: 2.2466e-04
Epoch 2/5
72000/72000 [==============================] - 7s 98us/sample - loss: 9.8142e-04 - mean_squared_error: 9.8142e-04 - val_loss: 8.4453e-05 - val_mean_squared_error: 8.4453e-05
Epoch 3/5
72000/72000 [==============================] - 7s 100us/sample - loss: 4.3428e-04 - mean_squared_error: 4.3428e-04 - val_loss: 5.7222e-05 - val_mean_squared_error: 5.7222e-05
Epoch 4/5
72000/72000 [==============================] - 8s 107us/sample - loss: 2.5518e-04 - mean_squared_error: 2.5518e-04 - val_loss: 5.7125e-05 - val_mean_squared_error: 5.7125e-05
Epoch 5/5
72000/72000 [==============================] - 7s 104us/sample - loss: 1.8229e-04 - mean_squared_error: 1.8229e-04 - val_loss: 

...

--- Starting trial: run-11
{'num_units': 750, 'dropout': 0.3, 'optimizer': 'sgd'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 10s 145us/sample - loss: 0.0160 - mean_squared_error: 0.0160 - val_loss: 0.0021 - val_mean_squared_error: 0.0021
Epoch 2/5
72000/72000 [==============================] - 9s 119us/sample - loss: 0.0087 - mean_squared_error: 0.0087 - val_loss: 0.0011 - val_mean_squared_error: 0.0011
Epoch 3/5
72000/72000 [==============================] - 8s 114us/sample - loss: 0.0069 - mean_squared_error: 0.0069 - val_loss: 6.8887e-04 - val_mean_squared_error: 6.8887e-04
Epoch 4/5
72000/72000 [==============================] - 11s 149us/sample - loss: 0.0057 - mean_squared_error: 0.0057 - val_loss: 4.6820e-04 - val_mean_squared_error: 4.6820e-04
Epoch 5/5
72000/72000 [==============================] - 10s 132us/sample - loss: 0.0049 - mean_squared_error: 0.0049 - val_loss: 3.4960e-04 - val_mean_squared_error: 3.4960e

--- Starting trial: run-12
{'num_units': 1000, 'dropout': 0.1, 'optimizer': 'adam'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 14s 194us/sample - loss: 0.0050 - mean_squared_error: 0.0050 - val_loss: 1.8205e-04 - val_mean_squared_error: 1.8205e-04
Epoch 2/5
72000/72000 [==============================] - 12s 171us/sample - loss: 8.0115e-04 - mean_squared_error: 8.0115e-04 - val_loss: 9.9490e-05 - val_mean_squared_error: 9.9490e-05
Epoch 3/5
72000/72000 [==============================] - 10s 142us/sample - loss: 3.8557e-04 - mean_squared_error: 3.8557e-04 - val_loss: 6.9295e-05 - val_mean_squared_error: 6.9295e-05
Epoch 4/5
72000/72000 [==============================] - 10s 134us/sample - loss: 2.2781e-04 - mean_squared_error: 2.2781e-04 - val_loss: 5.0844e-05 - val_mean_squared_error: 5.0844e-05
Epoch 5/5
72000/72000 [==============================] - 11s 153us/sample - loss: 1.5936e-04 - mean_squared_error: 1.5936e-04 - va

--- Starting trial: run-13
{'num_units': 1000, 'dropout': 0.1, 'optimizer': 'sgd'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 12s 165us/sample - loss: 0.0085 - mean_squared_error: 0.0085 - val_loss: 0.0023 - val_mean_squared_error: 0.0023
Epoch 2/5
72000/72000 [==============================] - 11s 159us/sample - loss: 0.0034 - mean_squared_error: 0.0034 - val_loss: 0.0012 - val_mean_squared_error: 0.0012
Epoch 3/5
72000/72000 [==============================] - 14s 197us/sample - loss: 0.0027 - mean_squared_error: 0.0027 - val_loss: 7.1551e-04 - val_mean_squared_error: 7.1551e-04
Epoch 4/5
72000/72000 [==============================] - 11s 157us/sample - loss: 0.0023 - mean_squared_error: 0.0023 - val_loss: 4.9163e-04 - val_mean_squared_error: 4.9163e-04
Epoch 5/5
72000/72000 [==============================] - 11s 155us/sample - loss: 0.0021 - mean_squared_error: 0.0021 - val_loss: 3.8004e-04 - val_mean_squared_error: 3.80

--- Starting trial: run-14
{'num_units': 1000, 'dropout': 0.3, 'optimizer': 'adam'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 13s 179us/sample - loss: 0.0063 - mean_squared_error: 0.0063 - val_loss: 2.0023e-04 - val_mean_squared_error: 2.0023e-04
Epoch 2/5
72000/72000 [==============================] - 12s 163us/sample - loss: 8.8158e-04 - mean_squared_error: 8.8158e-04 - val_loss: 9.5122e-05 - val_mean_squared_error: 9.5122e-05
Epoch 3/5
72000/72000 [==============================] - 12s 164us/sample - loss: 4.3569e-04 - mean_squared_error: 4.3569e-04 - val_loss: 4.2508e-05 - val_mean_squared_error: 4.2508e-05
Epoch 4/5
72000/72000 [==============================] - 11s 159us/sample - loss: 3.0697e-04 - mean_squared_error: 3.0697e-04 - val_loss: 4.8060e-05 - val_mean_squared_error: 4.8060e-05
10000/1 [=========================================================================================================================

--- Starting trial: run-15
{'num_units': 1000, 'dropout': 0.3, 'optimizer': 'sgd'}
Train on 72000 samples, validate on 18000 samples
Epoch 1/5
72000/72000 [==============================] - 12s 170us/sample - loss: 0.0133 - mean_squared_error: 0.0133 - val_loss: 0.0027 - val_mean_squared_error: 0.0027
Epoch 2/5
72000/72000 [==============================] - 11s 154us/sample - loss: 0.0077 - mean_squared_error: 0.0077 - val_loss: 0.0014 - val_mean_squared_error: 0.0014
Epoch 3/5
72000/72000 [==============================] - 12s 171us/sample - loss: 0.0060 - mean_squared_error: 0.0060 - val_loss: 8.0610e-04 - val_mean_squared_error: 8.0610e-04
Epoch 4/5
72000/72000 [==============================] - 15s 202us/sample - loss: 0.0051 - mean_squared_error: 0.0051 - val_loss: 5.2497e-04 - val_mean_squared_error: 5.2497e-04
Epoch 5/5
72000/72000 [==============================] - 15s 215us/sample - loss: 0.0044 - mean_squared_error: 0.0044 - val_loss: 3.7988e-04 - val_mean_squared_error: 3.79

It’s time to launch TensorBoard. Use the following commands to launch tensorboard.

In [23]:
%tensorboard --logdir logs/hparam_tuning

Reusing TensorBoard on port 6008 (pid 81772), started 0:43:05 ago. (Use '!kill 81772' to kill it.)

Once it is launched, you will see a beautiful dashboard. Click on the HPARAMS tab to see the hyperparameter logs.

In "Table View" all the hyperparameter combinations and the respective accuracy will be displayed in a beautiful table as. The left side of the dashboard provides a number of filtering capabilities such as sorting based on the metric, filtering based on specific type or value of hyperparameter, filtering based on status etc.

The Parallel Coordinates View shows each run as a line going through an axis for each hyperparameter and metric. The interactive plot allows us to mark a region which will highlight only the runs that pass through it. The units if each hyperparameter can also be changed between linear, logarithmic and quantile values. This is extremely useful in understanding the relationships between the hyperparameters. We can select the optimum hyperparameters just by selecting the least MSE (run your mouse over the line)

The Scatter Plot View plots each of the hyperparameter and the given metric against the metric.This helps us understand how different values of each parameter correlates to the metric.

LINKS:

https://analyticsindiamag.com/parameter-tuning-tensorboard/

https://www.tensorflow.org/tensorboard/hyperparameter_tuning_with_hparams

https://medium.com/ml-book/neural-networks-hyperparameter-tuning-in-tensorflow-2-0-a7b4e2b574a1

https://github.com/tensorflow/tensorboard/blob/master/tensorboard/plugins/hparams/summary_v2.py



IDEAS: 

- HP_LEARNING_RATE = hp.HParam("learning_rate", hp.RealInterval(1e-5, 1e-1))

- HP_L2 = hp.HParam('l2 regularizer', hp.RealInterval(.001,.01))